In [1]:
import pandas as pd
import matplotlib
import numpy as np
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)
import io
import plotly.graph_objs as go 
from plotly.offline import plot

In [2]:
#Imorting data
reviews = pd.read_csv("/home/eslam/Downloads/ITI_Python/ITI_Python_for_Data_Management/Task 3/data/winemag-data-130k-v2.csv", index_col=0)
reviews.head(2)

country                                        description   designation  \
0     Italy  Aromas include tropical fruit, broom, brimston...  Vulkà Bianco   
1  Portugal  This is ripe and fruity, a wine that is smooth...      Avidagos   

   points  price           province region_1 region_2    taster_name  \
0      87    NaN  Sicily & Sardinia     Etna      NaN  Kerin O’Keefe   
1      87   15.0              Douro      NaN      NaN     Roger Voss   

  taster_twitter_handle                                          title  \
0          @kerinokeefe              Nicosia 2013 Vulkà Bianco  (Etna)   
1            @vossroger  Quinta dos Avidagos 2011 Avidagos Red (Douro)   

          variety               winery  
0     White Blend              Nicosia  
1  Portuguese Red  Quinta dos Avidagos

In [3]:
#Replacing country name to be used later in a join
reviews['country']=reviews['country'].str.replace("US","United States")
reviews.head(3)

country                                        description  \
0          Italy  Aromas include tropical fruit, broom, brimston...   
1       Portugal  This is ripe and fruity, a wine that is smooth...   
2  United States  Tart and snappy, the flavors of lime flesh and...   

    designation  points  price           province           region_1  \
0  Vulkà Bianco      87    NaN  Sicily & Sardinia               Etna   
1      Avidagos      87   15.0              Douro                NaN   
2           NaN      87   14.0             Oregon  Willamette Valley   

            region_2    taster_name taster_twitter_handle  \
0                NaN  Kerin O’Keefe          @kerinokeefe   
1                NaN     Roger Voss            @vossroger   
2  Willamette Valley   Paul Gregutt           @paulgwine    

                                           title         variety  \
0              Nicosia 2013 Vulkà Bianco  (Etna)     White Blend   
1  Quinta dos Avidagos 2011 Avidagos Red (Douro)  Portuguese Red   
2  Rainstorm 2013 Pinot Gris (Willamette Valley)      Pinot Gris   

                winery  
0              Nicosia  
1  Quinta dos Avidagos  
2            Rainstorm

In [4]:
#Importing a dataframe containing countries and their corresponding codes to be used in go.Choropleth
cc = pd.read_csv("/home/eslam/Downloads/ITI_Python/ITI_Python_for_Data_Management/Task 3/data/2014_world_gdp_with_codes.csv")
#Renaming 'COUNTRY' column to be used in a join later
cc.rename(columns={'COUNTRY':'country'},inplace=True)
cc.head()

country  GDP (BILLIONS) CODE
0     Afghanistan           21.71  AFG
1         Albania           13.40  ALB
2         Algeria          227.80  DZA
3  American Samoa            0.75  ASM
4         Andorra            4.80  AND

In [5]:
#First graph: Scatter Plot
#Here, I wanted to know the top 10 countries in generating wine brands
BrandsPerCountry = reviews.loc[:,['country','designation']]
BrandsPerCountry.head()

country                         designation
0          Italy                        Vulkà Bianco
1       Portugal                            Avidagos
2  United States                                 NaN
3  United States                Reserve Late Harvest
4  United States  Vintner's Reserve Wild Child Block

In [6]:
#Adding country code column by merging to be used later in choropleth plot
BrandsPerCountryMerged = pd.merge(BrandsPerCountry,cc[['country','CODE']], on='country', how='left')
BrandsPerCountryMerged.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 129971 entries, 0 to 129970
Data columns (total 3 columns):
country        129908 non-null object
designation    92506 non-null object
CODE           129834 non-null object
dtypes: object(3)
memory usage: 4.0+ MB


In [7]:
#Grouping by country and country code and counting number of brands generated per country
BrandsPerCountryGrouped = BrandsPerCountryMerged.groupby(['country','CODE'], as_index=False)['designation'].count()
#Sorting result in a descending order
BrandsPerCountryGrouped.sort_values(by='designation', ascending=False, inplace=True)
# BrandsPerCountryGrouped.head()
#Selecting top 10 countries in brand generation
BPCGH = BrandsPerCountryGrouped.head(10)

In [8]:
import plotly.graph_objects as go
# import numpy as np

X = BPCGH['country']
Y = BPCGH['designation']
Z = BPCGH['designation']/300

fig = go.Figure(data=go.Scatter(x=X, y=Y, mode='markers', marker_size = Z))
fig.update_layout(
    title="Top 10 Countries in Wine Brand Generation",
    xaxis_title="Country",
    yaxis_title="No. of Brands",
#     legend_title="Legend Title",
    font=dict(
        family="Courier New, monospace",
        size=14,
        color="RebeccaPurple"
    )
)
# fig.update_traces(name='Wine Brands per Country', selector=dict(type='scatter'))

fig.show()

In [9]:
#Second Graph: Choropleth (1)
#In this graph, I wanted to know the average wine quality per state

#Importing a dataframe with states' codes to be used in the Choropleth plot
cols = ["code", "state"]
stateCode = pd.read_csv('/home/eslam/Downloads/ITI_Python/ITI_Python_for_Data_Management/Task 3/data/2011_us_ag_exports.csv',
                            usecols=cols)
#Changing column name from 'state' to 'province' to be used later in merging
stateCode.rename(columns={'state':'province'},inplace=True)
stateCode.head()

code    province
0   AL     Alabama
1   AK      Alaska
2   AZ     Arizona
3   AR    Arkansas
4   CA  California

In [10]:
#Selecting the desired columns
QualityPerState = reviews.loc[:,['province','points']]
#Grouping by state and aggregating
QualityperStateGrouped = QualityPerState.groupby('province',as_index=False)['points'].mean()
QualityperStateGrouped.head()

province     points
0            Achaia  85.800000
1   Aconcagua Costa  87.629630
2  Aconcagua Valley  88.163793
3            Aegean  88.954545
4       Agioritikos  86.333333

In [11]:
PricePerState = reviews.loc[:,['province','price']]
PriceperStateGrouped = PricePerState.groupby('province',as_index=False)['price'].mean()
PpSGM = pd.merge(stateCode, PriceperStateGrouped, on='province', how='left')
PpSGM.head()

code    province      price
0   AL     Alabama        NaN
1   AK      Alaska        NaN
2   AZ     Arizona  29.200000
3   AR    Arkansas        NaN
4   CA  California  39.041048

In [12]:
#Adding state code column by merging the 'stateCode' and 'QualityperStateGrouped' dataframes
QpSGM = pd.merge(stateCode, QualityperStateGrouped, on='province', how='left')
QpSGM.head()

code    province     points
0   AL     Alabama        NaN
1   AK      Alaska        NaN
2   AZ     Arizona  84.926829
3   AR    Arkansas        NaN
4   CA  California  88.627776

In [13]:
fig = go.Figure(data=go.Choropleth(
    locations=QpSGM['code'], # Spatial coordinates
    z = QpSGM['points'].astype(float), # Data to be color-coded
    locationmode = 'USA-states', # set of locations match entries in `locations`
    colorscale = 'Reds',
    colorbar_title = "Points",
))

fig.update_layout(
    title_text = 'Wine Quality per State',
    geo_scope='usa', # limit map scope to USA
)

fig.show()

In [14]:
#Follow Second Graph: Choropleth (2)
#In this graph, I wanted to compare the average wine quality per state to the average \n
# price per state. I know there are outliers in the price list which will affect \n
# the relation, but I couldn't exclude the outliers.
data1 = dict(type='choropleth',
            locations=QpSGM['code'],
            locationmode='USA-states',
             colorbar = dict(x=0.44),
             colorbar_title = 'Points',
#              colorscale='Reds',
            text=QpSGM['province'],
            z=QpSGM['points'].astype(float),
             geo = 'geo'
            ) 

data2 = dict(type='choropleth',
            locations=PpSGM['code'],
            locationmode='USA-states',
             colorbar = dict(x=0.95),
             colorbar_title = 'Price',
#              colorscale='Reds',
            text=PpSGM['province'],
            z=PpSGM['price'],
             geo = 'geo2'
            ) 

layout = dict()

layout['geo'] = dict(
        scope = 'usa',
        showland = True,
        landcolor = 'rgb(229, 229, 229)',
        showcountries = False,
        domain = dict( x = [0.0, 0.5], y = [0.0, 1.0] ),
        subunitcolor = "rgb(255, 255, 255)",
    )

layout['geo2'] = dict(
        scope = 'usa',
        showland = True,
        landcolor = 'rgb(229, 229, 229)',
        showcountries = False,
        domain = dict( x = [0.5, 1.0], y = [0.0, 1.0] ),
        subunitcolor = "rgb(255, 255, 255)",
    )
fig = go.Figure(data=[data1,data2], layout=layout)
fig.update_layout(width=720, title_text='Average Points per State (left) and Average Price per State (Right)')
fig.show()

# choromap = go.Figure(data=[data1,data2], layout=layout)
# plot(choromap)

In [15]:
#Follow Second Graph:Choropleth (3)
#This graph is an extension for the first graph (brand generation per country) \n
#except this time, I wanted to include all the countries.


fig = go.Figure(data=go.Choropleth(
    locations = BrandsPerCountryGrouped['CODE'],
    z = BrandsPerCountryGrouped['designation'],
    text = BrandsPerCountryGrouped['country'],
    
    autocolorscale=True,
    reversescale=True,
    marker_line_color='darkgray',
    marker_line_width=0.5,
    colorbar_title = 'Brands per Country',
))

fig.update_layout(
    title_text='Wine Brand Generation By Country',
    geo=dict(
        showframe=False,
        showcoastlines=False,
        projection_type='equirectangular'
    ),
    annotations = [dict(
        x=0.55,
        y=0.1,
        xref='paper',
        yref='paper',

        showarrow = True
    )]
)

fig.show()

In [16]:
#Third Graph: Heatmap Plot
#Does the review points affect wine price?

VarPriPoints = reviews.loc[:,['price','variety','points']]
VarPriPointsFilter = VarPriPoints.loc[VarPriPoints['variety'].isin(['White Blend','Zinfandel','Pinot Noir', 'Chardonnay'])]
VarPriPointsFilter.head(10)
VarPriPointsFilter.to_csv('~/Downloads/ITI_Python/ITI_Python_for_Data_Management/Task 3/data/VarPriPointsFilter.csv')


In [17]:

VarPriPointsG = VarPriPointsFilter.groupby(['variety','points'],as_index=False)['price'].mean()
VarPriPointsGF = VarPriPointsG[VarPriPointsG['price']<100]
v = VarPriPointsGF.pivot(index='variety', columns='points', values='price').fillna(0)
VarPriPointsG
# v

variety  points      price
0   Chardonnay      80  14.000000
1   Chardonnay      81  14.247059
2   Chardonnay      82  17.225806
3   Chardonnay      83  16.258160
4   Chardonnay      84  18.044034
..         ...     ...        ...
72   Zinfandel      93  39.392157
73   Zinfandel      94  48.605263
74   Zinfandel      95  52.545455
75   Zinfandel      96  60.000000
76   Zinfandel      97  50.000000

[77 rows x 3 columns]

In [18]:
fig = go.Figure(data=go.Heatmap(
        z=v,
#         z=VarPriPointGSample['price'],
        x=v.columns.values,
        y=v.index.to_numpy(),
        hoverongaps = False,
        colorscale='Viridis'))

fig.update_layout(
    title='Wine Va',
    xaxis_nticks=20
    )

fig.show()

In [19]:
#Fourth Graph: Surface Plot
PointsPrice = reviews.loc[:,['points','price']].dropna()
PointsPrice.head(2)

points  price
1      87   15.0
2      87   14.0

In [20]:
#Fourth Graph: Surface Plot
df = reviews.assign(n=0).groupby(['points', 'price'])['n'].count().reset_index()
df = df[df["price"] < 100]
v = df.pivot(index='price', columns='points', values='n').fillna(0).values.tolist()

In [21]:
iplot([go.Surface(z=v)])

In [25]:
#Fourth Graph: Surface Plot (My failed trials)
PointsPrice = reviews.loc[:,['points','price']].dropna()

PointsPrice.head(2)

points  price
1      87   15.0
2      87   14.0

In [26]:
Z = PointsPrice.to_numpy().tolist()

In [27]:
fig = go.Figure(data=[go.Surface(z=Z)])

fig.update_layout(title='Points and Prices', autosize=False,
                  width=500, height=500,
                  margin=dict(l=65, r=50, b=65, t=90))

fig.show()